In [0]:
##Start here
from pyspark.sql import SparkSession
from pyspark.sql import functions as F
spark.conf.set("spark.sql.legacy.timeParserPolicy","LEGACY")
spark = SparkSession.builder.appName('UberLyftProject').getOrCreate()
from pyspark.sql.functions import datediff,date_format,to_date,to_timestamp,from_unixtime,hour

  
url = "https://raw.githubusercontent.com/Anu282/Uber-Lyft-Cabs-Price/d82d82cdc3a554964ddcc7129f99a5192deb6307/cab_rides.csv"
from pyspark import SparkFiles
spark.sparkContext.addFile(url)
dfCabs = spark.read.csv("file://"+SparkFiles.get("cab_rides.csv"), header=True, inferSchema= True)
dfCabs=dfCabs.withColumn('time_stamp',from_unixtime((dfCabs.time_stamp/1000), 'yyyy-MM-dd HH:mm:ss.SSSS'))

In [0]:
dfCabs.show()

+--------+--------+--------------------+--------------------+----------------+-----+----------------+--------------------+--------------------+------------+
|distance|cab_type|          time_stamp|         destination|          source|price|surge_multiplier|                  id|          product_id|        name|
+--------+--------+--------------------+--------------------+----------------+-----+----------------+--------------------+--------------------+------------+
|    0.44|    Lyft|2018-12-16 09:30:...|       North Station|Haymarket Square|  5.0|             1.0|424553bb-7174-41e...|           lyft_line|      Shared|
|    0.44|    Lyft|2018-11-27 02:00:...|       North Station|Haymarket Square| 11.0|             1.0|4bd23055-6827-41c...|        lyft_premier|         Lux|
|    0.44|    Lyft|2018-11-28 01:00:...|       North Station|Haymarket Square|  7.0|             1.0|981a3613-77af-462...|                lyft|        Lyft|
|    0.44|    Lyft|2018-11-30 04:53:...|       North Stati

In [0]:
url = "https://raw.githubusercontent.com/Anu282/Uber-Lyft-Cabs-Price/main/weather.csv"
from pyspark import SparkFiles
spark.sparkContext.addFile(url)
dfWeather = spark.read.csv("file://"+SparkFiles.get("weather.csv"), header=True, inferSchema= True)
dfWeather=dfWeather.withColumn('time_stampw',from_unixtime((dfWeather.time_stamp), 'yyyy-MM-dd HH:mm:ss.SSSS'))

In [0]:
dfWeather.show()

+-----+--------------------+------+--------+------+----------+--------+-----+--------------------+
| temp|            location|clouds|pressure|  rain|time_stamp|humidity| wind|         time_stampw|
+-----+--------------------+------+--------+------+----------+--------+-----+--------------------+
|42.42|            Back Bay|   1.0| 1012.14|0.1228|1545003901|    0.77|11.25|2018-12-16 23:45:...|
|42.43|         Beacon Hill|   1.0| 1012.15|0.1846|1545003901|    0.76|11.32|2018-12-16 23:45:...|
| 42.5|   Boston University|   1.0| 1012.15|0.1089|1545003901|    0.76|11.07|2018-12-16 23:45:...|
|42.11|              Fenway|   1.0| 1012.13|0.0969|1545003901|    0.77|11.09|2018-12-16 23:45:...|
|43.13|  Financial District|   1.0| 1012.14|0.1786|1545003901|    0.75|11.49|2018-12-16 23:45:...|
|42.34|    Haymarket Square|   1.0| 1012.15|0.2068|1545003901|    0.77|11.49|2018-12-16 23:45:...|
|42.36|           North End|   1.0| 1012.15|0.2088|1545003901|    0.77|11.46|2018-12-16 23:45:...|
|42.21|   

In [0]:
dfCabs.schema

Out[152]: StructType(List(StructField(distance,DoubleType,true),StructField(cab_type,StringType,true),StructField(time_stamp,StringType,true),StructField(destination,StringType,true),StructField(source,StringType,true),StructField(price,DoubleType,true),StructField(surge_multiplier,DoubleType,true),StructField(id,StringType,true),StructField(product_id,StringType,true),StructField(name,StringType,true)))

In [0]:
dfWeather.schema
from pyspark.sql.functions import concat_ws

In [0]:
#dfCabs=dfCabs.withColumn('',concat(dfCabs.source,to_date(dfCabs.time_stamp),F.date_trunc('hour',hour(to_timestamp(dfCabs.time_stamp,'yyyy-MM-dd HH:mm:ss.SSSS')))))
#cab_df['merge_date'] = cab_df.source.astype(str) +" - "+ cab_df.date_time.dt.date.astype("str") +" - "+ cab_df.date_time.dt.hour.astype("str")
#df.withColumn("hour", F.date_trunc('hour',F.to_timestamp("timestamp","yyyy-MM-dd HH:mm:ss 'UTC'")))\
  #.show(truncate=False)
dfCabs.show()

+--------+--------+--------------------+--------------------+----------------+-----+----------------+--------------------+--------------------+------------+
|distance|cab_type|          time_stamp|         destination|          source|price|surge_multiplier|                  id|          product_id|        name|
+--------+--------+--------------------+--------------------+----------------+-----+----------------+--------------------+--------------------+------------+
|    0.44|    Lyft|2018-12-16 09:30:...|       North Station|Haymarket Square|  5.0|             1.0|424553bb-7174-41e...|           lyft_line|      Shared|
|    0.44|    Lyft|2018-11-27 02:00:...|       North Station|Haymarket Square| 11.0|             1.0|4bd23055-6827-41c...|        lyft_premier|         Lux|
|    0.44|    Lyft|2018-11-28 01:00:...|       North Station|Haymarket Square|  7.0|             1.0|981a3613-77af-462...|                lyft|        Lyft|
|    0.44|    Lyft|2018-11-30 04:53:...|       North Stati

In [0]:
from pyspark.sql.functions import datediff,date_format,to_date,to_timestamp,from_unixtime,hour,dayofweek
dfCabs=dfCabs.withColumn('hour',hour(to_timestamp(dfCabs.time_stamp,'yyyy-MM-dd HH:mm:ss.SSSS'))).\
              withColumn('date',to_date(dfCabs.time_stamp,'yyyy-MM-dd')).\
              withColumn('day',dayofweek(to_date(dfCabs.time_stamp,'yyyy-MM-dd'))).\
              withColumn('dayofweek',date_format(to_date(dfCabs.time_stamp,'yyyy-MM-dd'), "EEEE"))

dfCabs.show()


+--------+--------+--------------------+--------------------+----------------+-----+----------------+--------------------+--------------------+------------+----+----------+---+---------+
|distance|cab_type|          time_stamp|         destination|          source|price|surge_multiplier|                  id|          product_id|        name|hour|      date|day|dayofweek|
+--------+--------+--------------------+--------------------+----------------+-----+----------------+--------------------+--------------------+------------+----+----------+---+---------+
|    0.44|    Lyft|2018-12-16 09:30:...|       North Station|Haymarket Square|  5.0|             1.0|424553bb-7174-41e...|           lyft_line|      Shared|   9|2018-12-16|  1|   Sunday|
|    0.44|    Lyft|2018-11-27 02:00:...|       North Station|Haymarket Square| 11.0|             1.0|4bd23055-6827-41c...|        lyft_premier|         Lux|   2|2018-11-27|  3|  Tuesday|
|    0.44|    Lyft|2018-11-28 01:00:...|       North Station|Haym

In [0]:
dfCabsFinal=dfCabs.select("distance","cab_type","time_stamp","destination","source","price","surge_multiplier","id","product_id","name","date","hour","dayofweek",concat_ws('-',dfCabs.source,dfCabs.date,dfCabs.hour)
              .alias("placedatehour"))


In [0]:
dfWeather=dfWeather.withColumn('hourw',hour(to_timestamp(dfWeather.time_stampw,'yyyy-MM-dd HH:mm:ss.SSSS'))).\
              withColumn('datew',to_date(dfWeather.time_stampw,'yyyy-MM-dd')) #.\
              #withColumn('mergedateplace',dfCabs.source,dfCabs.date,dfCabs.hour
dfWeather.show()

+-----+--------------------+------+--------+------+----------+--------+-----+--------------------+-----+----------+
| temp|            location|clouds|pressure|  rain|time_stamp|humidity| wind|         time_stampw|hourw|     datew|
+-----+--------------------+------+--------+------+----------+--------+-----+--------------------+-----+----------+
|42.42|            Back Bay|   1.0| 1012.14|0.1228|1545003901|    0.77|11.25|2018-12-16 23:45:...|   23|2018-12-16|
|42.43|         Beacon Hill|   1.0| 1012.15|0.1846|1545003901|    0.76|11.32|2018-12-16 23:45:...|   23|2018-12-16|
| 42.5|   Boston University|   1.0| 1012.15|0.1089|1545003901|    0.76|11.07|2018-12-16 23:45:...|   23|2018-12-16|
|42.11|              Fenway|   1.0| 1012.13|0.0969|1545003901|    0.77|11.09|2018-12-16 23:45:...|   23|2018-12-16|
|43.13|  Financial District|   1.0| 1012.14|0.1786|1545003901|    0.75|11.49|2018-12-16 23:45:...|   23|2018-12-16|
|42.34|    Haymarket Square|   1.0| 1012.15|0.2068|1545003901|    0.77|1

In [0]:
dfWeatherFinal=dfWeather.select("temp","location","clouds","pressure","rain","time_stampw","humidity","wind","hourw","datew",concat_ws('-',dfWeather.location,dfWeather.datew,dfWeather.hourw)
              .alias("placedatehourw"))

In [0]:
#dfWeather.columns
dfWeatherFinal.columns
#dfCabs.columns
dfWeatherFinal=dfWeatherFinal.dropDuplicates(['placedatehourw'])

In [0]:
dfWeatherFinal.createOrReplaceTempView("weather")
dfCabsFinal.createOrReplaceTempView("Cabs")

In [0]:
%sql
select placedatehourw,* from weather order by placedatehourw
--select location,clouds,pressure  from weather where placedatehourw in (select placedatehour from cabs)

placedatehourw temp location clouds pressure rain time_stampw humidity wind hourw datew placedatehourw Back Bay-2018-11-26-10 40.83 Back Bay 1.0 1014.75 null 2018-11-26 10:05:10.0000 0.93 1.84 10 2018-11-26 Back Bay-2018-11-26-10 Back Bay-2018-11-26-11 40.14 Back Bay 0.94 1015.34 null 2018-11-26 11:35:08.0000 0.95 2.26 11 2018-11-26 Back Bay-2018-11-26-11 Back Bay-2018-11-26-12 40.52 Back Bay 0.89 1015.35 null 2018-11-26 12:35:08.0000 0.94 3.32 12 2018-11-26 Back Bay-2018-11-26-12 Back Bay-2018-11-26-13 42.19 Back Bay 0.89 1015.01 0.0062 2018-11-26 13:35:10.0000 0.91 3.61 13 2018-11-26 Back Bay-2018-11-26-13 Back Bay-2018-11-26-14 42.55 Back Bay 0.91 1014.84 0.0088 2018-11-26 14:05:09.0000 0.91 2.25 14 2018-11-26 Back Bay-2018-11-26-14 Back Bay-2018-11-26-15 44.28 Back Bay 0.89 1014.2 null 2018-11-26 15:35:08.0000 0.89 4.9 15 2018-11-26 Back Bay-2018-11-26-15 Back Bay-2018-11-26-16 45.16 Back Bay 0.84 1013.54 null 2018-11-26 16:35:08.0000 0.87 5.79 16 2018-11-26 Back Bay-2018-11-26-16 Back Bay-2018-11-26-17 45.49 Back Bay 1.0 1012.46 null 2018-11-26 17:35:10.0000 0.86 6.47 17 2018-11-26 Back Bay-2018-11-26-17 Back Bay-2018-11-26-18 45.39 Back Bay 1.0 1011.86 null 2018-11-26 18:35:09.0000 0.87 6.11 18 2018-11-26 Back Bay-2018-11-26-18 Back Bay-2018-11-26-19 45.98 Back Bay 0.92 1010.87 null 2018-11-26 19:35:10.0000 0.83 8.63 19 2018-11-26 Back Bay-2018-11-26-19 Back Bay-2018-11-26-20 45.21 Back Bay 0.88 1009.86 null 2018-11-26 20:35:09.0000 0.83 9.35 20 2018-11-26 Back Bay-2018-11-26-20 Back Bay-2018-11-26-21 44.55 Back Bay 0.91 1009.01 0.004 2018-11-26 21:35:08.0000 0.86 9.41 21 2018-11-26 Back Bay-2018-11-26-21 Back Bay-2018-11-26-22 44.92 Back Bay 0.99 1008.4 0.0093 2018-11-26 22:05:09.0000 0.87 7.47 22 2018-11-26 Back Bay-2018-11-26-22 Back Bay-2018-11-26-23 44.3 Back Bay 0.96 1007.81 0.1477 2018-11-26 23:42:13.0000 0.89 9.64 23 2018-11-26 Back Bay-2018-11-26-23 Back Bay-2018-11-26-3 41.04 Back Bay 0.87 1014.39 null 2018-11-26 03:40:45.0000 0.92 1.46 3 2018-11-26 Back Bay-2018-11-26-3 Back Bay-2018-11-26-4 40.63 Back Bay 0.86 1014.17 null 2018-11-26 04:40:53.0000 0.93 2.57 4 2018-11-26 Back Bay-2018-11-26-4 Back Bay-2018-11-26-5 40.65 Back Bay 0.93 1013.76 null 2018-11-26 05:13:03.0000 0.92 3.01 5 2018-11-26 Back Bay-2018-11-26-5 Back Bay-2018-11-26-6 40.52 Back Bay 1.0 1014.17 null 2018-11-26 06:24:05.0000 0.91 1.29 6 2018-11-26 Back Bay-2018-11-26-6 Back Bay-2018-11-26-7 41.07 Back Bay 0.98 1014.26 null 2018-11-26 07:46:10.0000 0.91 1.42 7 2018-11-26 Back Bay-2018-11-26-7 Back Bay-2018-11-26-8 40.81 Back Bay 1.0 1014.58 null 2018-11-26 08:34:05.0000 0.93 1.26 8 2018-11-26 Back Bay-2018-11-26-8 Back Bay-2018-11-26-9 40.89 Back Bay 1.0 1014.75 null 2018-11-26 09:29:09.0000 0.93 1.25 9 2018-11-26 Back Bay-2018-11-26-9 Back Bay-2018-11-27-0 43.96 Back Bay 1.0 1006.26 0.0497 2018-11-27 00:17:14.0000 0.9 9.86 0 2018-11-27 Back Bay-2018-11-27-0 Back Bay-2018-11-27-1 44.09 Back Bay 0.99 1005.3 0.1577 2018-11-27 01:18:34.0000 0.9 11.25 1 2018-11-27 Back Bay-2018-11-27-1 Back Bay-2018-11-27-10 44.56 Back Bay 0.99 990.78 0.0213 2018-11-27 10:15:20.0000 0.96 5.87 10 2018-11-27 Back Bay-2018-11-27-10 Back Bay-2018-11-27-11 44.76 Back Bay 0.99 989.77 null 2018-11-27 11:15:20.0000 0.96 3.3 11 2018-11-27 Back Bay-2018-11-27-11 Back Bay-2018-11-27-12 45.26 Back Bay 1.0 989.04 null 2018-11-27 12:15:20.0000 0.93 1.54 12 2018-11-27 Back Bay-2018-11-27-12 Back Bay-2018-11-27-13 44.66 Back Bay 0.95 988.29 null 2018-11-27 13:45:20.0000 0.9 6.64 13 2018-11-27 Back Bay-2018-11-27-13 Back Bay-2018-11-27-14 43.51 Back Bay 0.95 989.14 null 2018-11-27 14:45:20.0000 0.89 11.94 14 2018-11-27 Back Bay-2018-11-27-14 Back Bay-2018-11-27-15 40.92 Back Bay 1.0 989.81 null 2018-11-27 15:45:20.0000 0.87 9.39 15 2018-11-27 Back Bay-2018-11-27-15 Back Bay-2018-11-27-16 40.92 Back Bay 0.97 989.79 null 2018-11-27 16:45:20.0000 0.84 9.83 16 2018-11-27 Back Bay-2018-11-27-16 Back Bay-2018-11-27-17 41.4 Back Bay 0.9 989.88 null 2018-11-27 17:45:20.0000 0.78 10.72 17 

In [0]:
%sql
select placedatehour,* from cabs order by placedatehour

placedatehour distance cab_type time_stamp destination source price surge_multiplier id product_id name date hour dayofweek placedatehour Back Bay-2018-11-26-10 6.26 Uber 2018-11-26 10:41:09.0000 South Station Back Bay 19.5 1.0 2d093677-3240-4233-85be-7a48a94485bb 6f72dfc5-27f1-42e8-84db-ccc7a75f6969 UberXL 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 6.26 Uber 2018-11-26 10:41:09.0000 South Station Back Bay 12.0 1.0 ef6e9c46-0504-47c7-a0c9-762156592772 9a0e7b09-b92b-4c41-9779-2ad22b4d779d WAV 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 2.32 Uber 2018-11-26 10:47:09.0000 Haymarket Square Back Bay 16.0 1.0 0a07e6d1-c65f-4045-90fd-ce3b57282803 6f72dfc5-27f1-42e8-84db-ccc7a75f6969 UberXL 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 1.45 Lyft 2018-11-26 10:23:09.0000 Fenway Back Bay 13.5 1.0 1066f8ae-bf05-4bb9-8750-6e037b90e012 lyft_premier Lux 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 6.26 Uber 2018-11-26 10:41:09.0000 South Station Back Bay 12.0 1.0 f55ab5ac-c9c6-4047-99d3-35d1a1799a41 997acbb5-e102-41e1-b155-9df7de0a73f2 UberPool 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 1.22 Uber 2018-11-26 10:32:10.0000 Northeastern University Back Bay 7.0 1.0 220a4eb5-fafc-471e-9b95-2c1244732652 997acbb5-e102-41e1-b155-9df7de0a73f2 UberPool 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 2.67 Lyft 2018-11-26 10:44:09.0000 South Station Back Bay 5.0 1.0 2ff37a12-b6a0-4b3f-82d3-c2059b78ad59 lyft_line Shared 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 1.43 Lyft 2018-11-26 10:53:09.0000 Fenway Back Bay 11.0 1.0 858494dc-058e-4e3e-8694-4434fc8cb730 lyft_plus Lyft XL 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 2.31 Lyft 2018-11-26 10:56:09.0000 Haymarket Square Back Bay 13.5 1.5 4fee8315-ca30-4c43-9da8-81c082cc8a37 lyft Lyft 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 2.33 Uber 2018-11-26 10:47:09.0000 North End Back Bay 19.5 1.0 d2f7dd59-f4c6-4b5a-a811-d8b36828d537 6c84fd89-3f11-4782-9b50-97c468b19529 Black 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 1.53 Lyft 2018-11-26 10:08:10.0000 Boston University Back Bay 16.5 1.0 a0a46b48-9cf0-408f-8e93-f90ac1284c8f lyft_lux Lux Black 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 1.44 Uber 2018-11-26 10:38:10.0000 Boston University Back Bay 17.0 1.0 d60eb784-5d65-4986-80b5-bb7c05186f0a 6c84fd89-3f11-4782-9b50-97c468b19529 Black 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 2.84 Uber 2018-11-26 10:56:09.0000 North End Back Bay 17.0 1.0 81c16aec-b2fe-411a-b06d-09f5e6087495 6f72dfc5-27f1-42e8-84db-ccc7a75f6969 UberXL 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 1.08 Uber 2018-11-26 10:32:10.0000 Northeastern University Back Bay 11.0 1.0 ee28a68b-358d-47f6-83fb-9a723906154b 6f72dfc5-27f1-42e8-84db-ccc7a75f6969 UberXL 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 1.34 Uber 2018-11-26 10:53:09.0000 Fenway Back Bay 8.5 1.0 c14203ef-b7c7-4f6a-a713-d63ac22da3aa 55c66225-fbe7-4fd5-9072-eab1ece5e23e UberX 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 2.33 Uber 2018-11-26 10:29:09.0000 North End Back Bay null 1.0 70809690-8f33-4c80-8a4a-c9b3cbd71721 8cf7e821-f0d3-49c6-8eba-e679c0ebcf6a Taxi 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 1.43 Lyft 2018-11-26 10:53:09.0000 Fenway Back Bay 13.5 1.0 14fa6614-d416-4582-aa66-7ea745996149 lyft_premier Lux 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 1.34 Uber 2018-11-26 10:14:10.0000 Fenway Back Bay 6.5 1.0 b8dfcc5e-7ca2-45f0-a36c-7f065204bdb2 997acbb5-e102-41e1-b155-9df7de0a73f2 UberPool 2018-11-26 10 Monday Back Bay-2018-11-26-10 Back Bay-2018-11-26-10 1.07 Lyft 2018-11-26 10:56:09.0000 Northeastern University Back Bay 10.5 1.0 182c93a9-7ea2-4984-9583-2d687d6eaab0 lyft_plus Lyft XL 2018-11-26 10 Monday B

In [0]:
merged_df=dfCabsFinal.join(dfWeatherFinal,dfCabsFinal.placedatehour ==  dfWeatherFinal.placedatehourw,"inner")

merged_df.show(10000)

+--------+--------+--------------------+--------------------+--------------------+-----+----------------+--------------------+--------------------+------------+----------+----+---------+--------------------+-----+--------------------+------+--------+------+--------------------+--------+-----+-----+----------+--------------------+
|distance|cab_type|          time_stamp|         destination|              source|price|surge_multiplier|                  id|          product_id|        name|      date|hour|dayofweek|       placedatehour| temp|            location|clouds|pressure|  rain|         time_stampw|humidity| wind|hourw|     datew|      placedatehourw|
+--------+--------+--------------------+--------------------+--------------------+-----+----------------+--------------------+--------------------+------------+----------+----+---------+--------------------+-----+--------------------+------+--------+------+--------------------+--------+-----+-----+----------+--------------------+
|   

In [0]:
merged_df=merged_df.fillna(0, subset=['rain'])

In [0]:
merged_df.show()

+--------+--------+--------------------+--------------------+----------------+-----+----------------+--------------------+--------------------+------------+----------+----+---------+--------------------+-----+----------------+------+--------+------+--------------------+--------+-----+-----+----------+--------------------+
|distance|cab_type|          time_stamp|         destination|          source|price|surge_multiplier|                  id|          product_id|        name|      date|hour|dayofweek|       placedatehour| temp|        location|clouds|pressure|  rain|         time_stampw|humidity| wind|hourw|     datew|      placedatehourw|
+--------+--------+--------------------+--------------------+----------------+-----+----------------+--------------------+--------------------+------------+----------+----+---------+--------------------+-----+----------------+------+--------+------+--------------------+--------+-----+-----+----------+--------------------+
|    0.44|    Lyft|2018-12-1

In [0]:
#merged_df.dropDuplicates().count()
merged_df.count()


Out[230]: 690107

In [0]:
finaldf=merged_df.select("distance","cab_type","time_stamp","destination","source","price","surge_multiplier","id","product_id","name","temp","location","clouds","pressure","rain","humidity","wind","hour","date","dayofweek","placedatehour")
finaldf.show()

+--------+--------+--------------------+--------------------+----------------+-----+----------------+--------------------+--------------------+------------+-----+----------------+------+--------+------+--------+-----+----+----------+---------+--------------------+
|distance|cab_type|          time_stamp|         destination|          source|price|surge_multiplier|                  id|          product_id|        name| temp|        location|clouds|pressure|  rain|humidity| wind|hour|      date|dayofweek|       placedatehour|
+--------+--------+--------------------+--------------------+----------------+-----+----------------+--------------------+--------------------+------------+-----+----------------+------+--------+------+--------+-----+----+----------+---------+--------------------+
|    0.44|    Lyft|2018-12-16 09:30:...|       North Station|Haymarket Square|  5.0|             1.0|424553bb-7174-41e...|           lyft_line|      Shared|38.46|Haymarket Square|  0.29| 1022.25|   0.0|   

In [0]:
finaldf.count()

Out[232]: 690107

In [0]:
finaldf.schema

Out[233]: StructType(List(StructField(distance,DoubleType,true),StructField(cab_type,StringType,true),StructField(time_stamp,StringType,true),StructField(destination,StringType,true),StructField(source,StringType,true),StructField(price,DoubleType,true),StructField(surge_multiplier,DoubleType,true),StructField(id,StringType,true),StructField(product_id,StringType,true),StructField(name,StringType,true),StructField(temp,DoubleType,true),StructField(location,StringType,true),StructField(clouds,DoubleType,true),StructField(pressure,DoubleType,true),StructField(rain,DoubleType,false),StructField(humidity,DoubleType,true),StructField(wind,DoubleType,true),StructField(hour,IntegerType,true),StructField(date,DateType,true),StructField(dayofweek,StringType,true),StructField(placedatehour,StringType,false)))

In [0]:
from pyspark.sql.functions import col

In [0]:
finaldf=finaldf.filter(col("price").isNotNull())

In [0]:
finaldf=finaldf.filter(col("rain").isNotNull())

In [0]:
finaldf=finaldf.filter(col("placedatehour").isNotNull())
#dropping multiple values for placedatehour
#finaldf=finaldf.dropDuplicates(['placedatehour'])

In [0]:
finaldf.count()

Out[333]: 329140

In [0]:
finaldf=finaldf.filter("cab_type=='Uber'")

In [0]:
finaldf.count()

Out[335]: 329140

In [0]:
finaldf.schema

Out[336]: StructType(List(StructField(distance,DoubleType,true),StructField(cab_type,StringType,true),StructField(time_stamp,StringType,true),StructField(destination,StringType,true),StructField(source,StringType,true),StructField(price,DoubleType,true),StructField(surge_multiplier,DoubleType,true),StructField(id,StringType,true),StructField(product_id,StringType,true),StructField(name,StringType,true),StructField(temp,DoubleType,true),StructField(location,StringType,true),StructField(clouds,DoubleType,true),StructField(pressure,DoubleType,true),StructField(rain,DoubleType,false),StructField(humidity,DoubleType,true),StructField(wind,DoubleType,true),StructField(hour,IntegerType,true),StructField(date,DateType,true),StructField(dayofweek,StringType,true),StructField(placedatehour,StringType,false)))

In [0]:
finaldf.createOrReplaceTempView("merged")

In [0]:
#finaldf.write.csv('/FileStore/tables/mergedfinal.csv')

In [0]:
%sql 
select * from merged 

distance cab_type time_stamp destination source price surge_multiplier id product_id name temp location clouds pressure rain humidity wind hour date dayofweek placedatehour 0.44 Lyft 2018-12-16 09:30:07.0000 North Station Haymarket Square 5.0 1.0 424553bb-7174-41ea-aeb4-fe06d4f4b9d7 lyft_line Shared 38.46 Haymarket Square 0.29 1022.25 0.0 0.76 7.68 9 2018-12-16 Sunday Haymarket Square-2018-12-16-9 0.44 Lyft 2018-11-27 02:00:23.0000 North Station Haymarket Square 11.0 1.0 4bd23055-6827-41c6-b23b-3c491f24e74d lyft_premier Lux 44.31 Haymarket Square 1.0 1003.17 0.1123 0.9 13.69 2 2018-11-27 Tuesday Haymarket Square-2018-11-27-2 0.44 Lyft 2018-11-30 04:53:02.0000 North Station Haymarket Square 26.0 1.0 c2d88af2-d278-4bfd-a8d0-29ca77cc5512 lyft_luxsuv Lux Black XL 35.08 Haymarket Square 0.0 1013.71 0.0 0.7 5.25 4 2018-11-30 Friday Haymarket Square-2018-11-30-4 0.44 Lyft 2018-11-29 03:49:20.0000 North Station Haymarket Square 9.0 1.0 e0126e1f-8ca9-4f2e-82b3-50505a09db9a lyft_plus Lyft XL 37.58 Haymarket Square 0.42 998.64 0.0 0.71 11.3 3 2018-11-29 Thursday Haymarket Square-2018-11-29-3 0.44 Lyft 2018-12-17 18:25:12.0000 North Station Haymarket Square 16.5 1.0 f6f6d7e4-3e18-4922-a5f5-181cdd3fa6f2 lyft_lux Lux Black 40.78 Haymarket Square 0.93 1000.15 0.0 0.79 7.55 18 2018-12-17 Monday Haymarket Square-2018-12-17-18 1.08 Lyft 2018-11-26 05:03:00.0000 Northeastern University Back Bay 10.5 1.0 462816a3-820d-408b-8549-0b39e82f65ac lyft_plus Lyft XL 40.65 Back Bay 0.93 1013.76 0.0 0.92 3.01 5 2018-11-26 Monday Back Bay-2018-11-26-5 1.08 Lyft 2018-12-02 19:53:04.0000 Northeastern University Back Bay 16.5 1.0 474d6376-bc59-4ec9-bf57-4e6d6faeb165 lyft_lux Lux Black 50.49 Back Bay 1.0 1004.05 0.0 0.92 2.46 19 2018-12-02 Sunday Back Bay-2018-12-02-19 1.08 Lyft 2018-12-03 06:28:02.0000 Northeastern University Back Bay 3.0 1.0 4f9fee41-fde3-4767-bbf1-a00e108701fb lyft_line Shared 44.85 Back Bay 0.89 1000.7 0.0 0.95 1.53 6 2018-12-03 Monday Back Bay-2018-12-03-6 1.08 Lyft 2018-11-27 10:45:22.0000 Northeastern University Back Bay 27.5 1.0 8612d909-98b8-4454-a093-30bd48de0cb3 lyft_luxsuv Lux Black XL 44.56 Back Bay 0.99 990.78 0.0213 0.96 5.87 10 2018-11-27 Tuesday Back Bay-2018-11-27-10 1.08 Lyft 2018-11-30 16:13:03.0000 Northeastern University Back Bay 13.5 1.0 9043bf77-1d45-4a93-9520-a083e0277f16 lyft_premier Lux 41.78 Back Bay 0.15 1016.57 0.0 0.57 2.51 16 2018-11-30 Friday Back Bay-2018-11-30-16 1.08 Lyft 2018-11-28 19:23:07.0000 Northeastern University Back Bay 7.0 1.0 d859ec69-b3ff-4af8-9abd-441e31430c94 lyft Lyft 41.09 Back Bay 1.0 991.83 0.0 0.64 9.45 19 2018-11-28 Wednesday Back Bay-2018-11-28-19 1.11 Uber 2018-11-30 22:13:01.0000 West End North End 12.0 1.0 009e9c53-074d-43cf-aef2-0fbc7a47ed3d 6f72dfc5-27f1-42e8-84db-ccc7a75f6969 UberXL 38.65 North End 0.96 1017.23 0.0 0.65 3.13 22 2018-11-30 Friday North End-2018-11-30-22 1.11 Uber 2018-12-13 10:50:11.0000 West End North End 16.0 1.0 23f145da-f0c1-4d1f-a184-496bc003a7db 6c84fd89-3f11-4782-9b50-97c468b19529 Black 20.12 North End 0.43 1031.07 0.0 0.64 3.88 10 2018-12-13 Thursday North End-2018-12-13-10 1.11 Uber 2018-12-13 19:15:03.0000 West End North End 7.5 1.0 357559cb-8c58-4278-a41a-e33b2e0997a3 55c66225-fbe7-4fd5-9072-eab1ece5e23e UberX 32.75 North End 0.51 1033.75 0.0 0.57 1.9 19 2018-12-13 Thursday North End-2018-12-13-19 1.11 Uber 2018-12-16 23:55:11.0000 West End North End 7.5 1.0 50ef1165-9d23-416c-a65c-18906207b295 9a0e7b09-b92b-4c41-9779-2ad22b4d779d WAV 42.36 North End 1.0 1012.15 0.2088 0.77 11.46 23 2018-12-16 Sunday North End-2018-12-16-23 1.11 Uber 2018-12-14 00:40:07.0000 West End North End 26.0 1.0 91c4861c-1780-42b0-bca1-bbd64a422cc3 6d318bcc-22a3-4af6-bddd-b409bfce1546 Black SUV 30.07 North End 0.69 1034.97 0.0 0.68 1.98 0 2018-12-14 Friday North End-2018-12-14-0 1.11 Uber 2018-11-29 19:18:00.0000 West End North End 5.5 1.0 e219e545-a006-4936-a6cc-7d00adf0e418 997acbb5-e102-41e1-b155-9df7de0a73f2 UberPool 42.48 North End 0.58 1007.66 0.0 0.54 10.84 19 2018-11-29 Thur

In [0]:
data=finaldf.select(['dayofweek','distance','hour','temp','clouds','pressure','humidity','wind','rain','price','surge_multiplier','product_id'])
#data=finaldf.select(['cab_type','name','product_id','source','destination','price','surge_multiplier'])

In [0]:
train_data,test_data=data.randomSplit([0.7,0.3])

In [0]:

data.schema

Out[314]: StructType(List(StructField(dayofweek,StringType,true),StructField(distance,DoubleType,true),StructField(hour,IntegerType,true),StructField(temp,DoubleType,true),StructField(clouds,DoubleType,true),StructField(pressure,DoubleType,true),StructField(humidity,DoubleType,true),StructField(wind,DoubleType,true),StructField(rain,DoubleType,false),StructField(price,DoubleType,true),StructField(surge_multiplier,DoubleType,true),StructField(product_id,StringType,true)))

In [0]:
train_data.show(500)

+---------+--------+----+-----+------+--------+--------+----+----+-----+----------------+--------------------+
|dayofweek|distance|hour| temp|clouds|pressure|humidity|wind|rain|price|surge_multiplier|          product_id|
+---------+--------+----+-----+------+--------+--------+----+----+-----+----------------+--------------------+
|   Friday|    0.03|   0|38.34|  0.09| 1011.72|    0.64|8.23| 0.0|  8.5|             1.0|6f72dfc5-27f1-42e...|
|   Friday|    0.03|   2|36.36|   0.0| 1012.38|    0.68|6.79| 0.0|  7.0|             1.0|55c66225-fbe7-4fd...|
|   Friday|    0.03|   9|26.63|  0.44| 1034.02|    0.81|2.39| 0.0|  7.0|             1.0|55c66225-fbe7-4fd...|
|   Friday|    0.03|  18|44.34|  0.19| 1029.99|    0.61|3.39| 0.0|  5.5|             1.0|997acbb5-e102-41e...|
|   Friday|     0.3|   3|29.92|  0.68| 1034.98|    0.71|1.94| 0.0|  8.5|             1.0|6f72dfc5-27f1-42e...|
|   Friday|    0.35|   7| 30.5|   0.0| 1015.05|    0.83|2.47| 0.0|  7.0|             1.0|997acbb5-e102-41e...|
|

#Linear Regression

In [0]:
# Import the required libraries
 
from pyspark.ml.regression import LinearRegression
from pyspark.ml.feature import VectorAssembler,StringIndexer
from pyspark.ml import Pipeline

In [0]:
dayofweek_indexer = StringIndexer(inputCol='dayofweek',outputCol='dayofweek_index',handleInvalid='keep')
##name_indexer = StringIndexer(inputCol='name',outputCol='name_index',handleInvalid='keep')
product_id_indexer = StringIndexer(inputCol='product_id',outputCol='product_id_index',handleInvalid='keep')

##source_indexer = StringIndexer(inputCol='source',outputCol='source_index',handleInvalid='keep')
##destination_indexer = StringIndexer(inputCol='destination',outputCol='destination_index',handleInvalid='keep')

##cab_type_indexer = StringIndexer(inputCol='cab_type',outputCol='cab_type_index',handleInvalid='keep')
 

In [0]:
assembler =  VectorAssembler(inputCols=['dayofweek_index','product_id_index','distance','hour','temp','clouds','pressure','humidity','wind','rain','surge_multiplier'],
                          outputCol="features")

In [0]:
pipe = Pipeline(stages=[dayofweek_indexer,product_id_indexer,assembler])

In [0]:
fitted_pipe=pipe.fit(train_data)

In [0]:
train_data=fitted_pipe.transform(train_data)

In [0]:
lr_model = LinearRegression(labelCol='price')

In [0]:
fit_model = lr_model.fit(train_data.select(['features','price']))

In [0]:
test_data=fitted_pipe.transform(test_data)

In [0]:
results = fit_model.transform(test_data)

In [0]:
results.select(['price','prediction']).show()

+-----+------------------+
|price|        prediction|
+-----+------------------+
|  7.0|12.890355713289052|
|  7.0|13.285730845735547|
| 16.0|10.908368864298398|
|  5.5| 10.07769506353037|
|  8.0|13.546481184251201|
|  7.0|13.567589761857505|
|  7.0| 9.151612868931464|
| 26.0|11.782984309048231|
| 12.0|12.647041329507415|
|  7.0| 13.50564458252666|
|  7.0|13.484695573432711|
| 15.5| 10.84642724917836|
|  5.5| 9.989448427988728|
|  8.5|12.627716752243082|
|  7.0|13.526904445712805|
|  8.5|12.647481670961355|
| 10.5|12.647481670961355|
| 19.5|  10.8951494313633|
|  7.0| 9.158949010366866|
|  5.5|10.042802987985025|
+-----+------------------+
only showing top 20 rows



In [0]:
test_results = fit_model.evaluate(test_data)

In [0]:
test_results.residuals.show()

+-------------------+
|          residuals|
+-------------------+
| -5.890355713289052|
|-6.2857308457355465|
|  5.091631135701602|
| -4.577695063530371|
| -5.546481184251201|
| -6.567589761857505|
|-2.1516128689314638|
| 14.217015690951769|
|-0.6470413295074149|
|  -6.50564458252666|
| -6.484695573432711|
|   4.65357275082164|
| -4.489448427988728|
|-4.1277167522430815|
| -6.526904445712805|
| -4.147481670961355|
| -2.147481670961355|
|    8.6048505686367|
|-2.1589490103668663|
| -4.542802987985025|
+-------------------+
only showing top 20 rows



In [0]:
test_results.rootMeanSquaredError

Out[330]: 7.939625994914657

In [0]:
test_results.r2 ## this r2 value was generated using rain,humidity,temp and other details from weather df

Out[331]: 0.14288338518303922

In [0]:
%sql

select count(*) from merged

count(1) 635242

#Random Forest Regression

In [0]:
data=finaldf.select(['dayofweek','distance','hour','temp','clouds','pressure','humidity','wind','rain','price'])

In [0]:
from pyspark.ml.regression import LinearRegression,RandomForestRegressor
from pyspark.ml.feature import VectorAssembler,StringIndexer
from pyspark.ml import Pipeline

In [0]:
train_data,test_data=data.randomSplit([0.7,0.3],seed=12345)

In [0]:
rf_model=RandomForestRegressor(featuresCol="features",labelCol='price')

In [0]:
dayofweek_indexer = StringIndexer(inputCol='dayofweek',outputCol='dayofweek_index',handleInvalid='keep')
 

In [0]:
assembler =  VectorAssembler(inputCols=['dayofweek_index','distance','hour','temp','clouds','pressure','humidity','wind','rain'],
                          outputCol="features")

In [0]:
pipe = Pipeline(stages=[dayofweek_indexer,assembler])

In [0]:
fitted_pipe=pipe.fit(train_data)

In [0]:
train_data=fitted_pipe.transform(train_data)

In [0]:
fit_model = rf_model.fit(train_data.select(['features','price']))


In [0]:
test_data=fitted_pipe.transform(test_data)
results = fit_model.transform(test_data)

results.select(['price','prediction']).show()

+-----+------------------+
|price|        prediction|
+-----+------------------+
|  7.0|13.192380724446718|
|  5.5|13.316834960979339|
|  7.0|13.123968489734846|
|  7.5| 13.37432025039891|
| 15.0|13.388214367668468|
|  7.0|13.206187220360212|
|  7.0| 13.19135027864285|
|  8.5|13.175550411449578|
| 26.5|13.279296392655368|
| 15.0|13.197813018192463|
|  5.5|13.349023621611474|
|  7.0|13.545308471784661|
|  7.0|13.316834960979339|
|  7.0|13.291142171371893|
| 27.5| 13.37432025039891|
|  9.5| 13.29283433045153|
|  7.0|13.388214367668468|
|  7.0|13.193461930567546|
| 15.0|13.129456046249203|
|  7.0|13.136638267887724|
+-----+------------------+
only showing top 20 rows



In [0]:
from pyspark.ml.evaluation import RegressionEvaluator
evaluate = RegressionEvaluator(
    labelCol="price", predictionCol="prediction", metricName="rmse")

# Calculating the root mean square value for the model.
rmse = evaluate.evaluate(results)
print("Root Mean Squared Error (RMSE) on test data = %g" % rmse)

Root Mean Squared Error (RMSE) on test data = 8.11457


In [0]:
# Creating a another Regression Evaluator object for calculating r2 score.
evaluate1 = RegressionEvaluator(
    labelCol="price", predictionCol="prediction", metricName="r2")

r2 = evaluate1.evaluate(results)
print("R Squared (R2) on test data = %g" % r2)

R Squared (R2) on test data = 0.101328
